# TP 2

## Imports

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
import matplotlib
import plotly as py
import plotly.express as px 
import matplotlib.ticker as ticker
plt.style.use('default')
import plotly.offline as opy
import plotly.figure_factory as ff
import plotly.io as pio
from wordcloud import WordCloud
from datetime import datetime
from datetime import timedelta

sns.set(style="whitegrid")

pd.options.display.float_format = '{:20,.2f}'.format 

import warnings
warnings.filterwarnings('ignore')

In [2]:
from sklearn.datasets import make_classification
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RepeatedStratifiedKFold

from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import make_scorer, accuracy_score
from sklearn.model_selection import train_test_split, GridSearchCV

### catboost

In [3]:
#Ejecutar si no funciona el import
!pip3 install catboost

     |████████████████████████████████| 65.8MB 79kB/s 


In [4]:
from catboost import CatBoostClassifier, Pool

### lightgbm

In [ ]:
!pip3 install lightgbm

In [ ]:
import lightgbm as lgb
#from lightgbm import LGBMClassifier

## lectura de datos

In [5]:
entrenamiento = pd.read_csv('Training.csv')
entrenamiento.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16947 entries, 0 to 16946
Data columns (total 52 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   ID                                  16947 non-null  int64  
 1   Region                              16947 non-null  object 
 2   Territory                           16947 non-null  object 
 3   Pricing, Delivery_Terms_Quote_Appr  16947 non-null  int64  
 4   Pricing, Delivery_Terms_Approved    16947 non-null  int64  
 5   Bureaucratic_Code_0_Approval        16947 non-null  int64  
 6   Bureaucratic_Code_0_Approved        16947 non-null  int64  
 7   Submitted_for_Approval              16947 non-null  int64  
 8   Bureaucratic_Code                   16947 non-null  object 
 9   Account_Created_Date                16947 non-null  object 
 10  Source                              16947 non-null  object 
 11  Billing_Country                     16947

In [6]:
testeo = pd.read_csv('Test.csv')
testeo.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2551 entries, 0 to 2550
Data columns (total 51 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   ID                                  2551 non-null   int64  
 1   Region                              2551 non-null   object 
 2   Territory                           2551 non-null   object 
 3   Pricing, Delivery_Terms_Quote_Appr  2551 non-null   int64  
 4   Pricing, Delivery_Terms_Approved    2551 non-null   int64  
 5   Bureaucratic_Code_0_Approval        2551 non-null   int64  
 6   Bureaucratic_Code_0_Approved        2551 non-null   int64  
 7   Submitted_for_Approval              2551 non-null   int64  
 8   Bureaucratic_Code                   2551 non-null   object 
 9   Account_Created_Date                2551 non-null   object 
 10  Source                              2551 non-null   object 
 11  Billing_Country                     2551 no

In [7]:
#hemisferios = pd.read_csv('hemisferios.csv')
#hemisferios = convertirATipo(hemisferios,['Billing_Country','hemisferio'],'category')
#hemisferios.info()

## prosesamiento de los df

### modificaciones de oportunidad

In [8]:
def convertirATiempo(df,lista):
    for columna in lista:
        df[columna] = pd.to_datetime(df[columna])
    return df

def convertirATipo(df,lista,tipo):
    for columna in lista:
        df[columna] = df[columna].astype(tipo)
    return df

def convertirAFlotante(df,lista):
    for columna in lista:
        df[columna] = df[columna].apply(lambda x: None if (x == "None" or x == "Other") else float(x))
    return df

def establecerTipos(df):
    """cambia los tipos de las columnas"""
    
    #fechas
    listaDeColumnasFechas = ['Account_Created_Date','Opportunity_Created_Date','Quote_Expiry_Date','Last_Modified_Date','Delivery_Year','Planned_Delivery_End_Date','Planned_Delivery_Start_Date']
    df = convertirATiempo(df,listaDeColumnasFechas)
    #enteros
    listaDeColumnasEnteras = ['ID','Opportunity_ID']
    convertirATipo(df,listaDeColumnasEnteras,'int')
    #decimales
    listaDeColumnasEnteras = ['Price','ASP','ASP_(converted)','Total_Taxable_Amount','Total_Amount']
    convertirAFlotante(df,listaDeColumnasEnteras)
    #booleanos
    listaDeColumnasBooleanas = ['Pricing, Delivery_Terms_Quote_Appr','Pricing, Delivery_Terms_Approved','Bureaucratic_Code_0_Approval','Bureaucratic_Code_0_Approved']
    convertirATipo(df,listaDeColumnasBooleanas,'bool')
    #categoricas
    listaDeColumnasCategoricas = ['Product_Category_B','Product_Family','Region','Territory','Bureaucratic_Code','Source ','Billing_Country','Account_Name','Opportunity_Name']
    convertirATipo(df,listaDeColumnasCategoricas,'category')
    return df

In [9]:
def agregarHemisferios(df):
  #df.reset_index()
  df = df.merge(hemisferios,how='left',on='Billing_Country')
  df['hemisferio'] = df['hemisferio'].apply(lambda x: 'Desconocido' if (x != 'Norte' and x != 'Sur') else x)
  convertirATipo(df,['hemisferio','Billing_Country'],'category')
  #df.set_index('Opportunity_ID')
  return df

In [10]:
def eliminarColumnasSinImportancia(df):
    #"Last_Activity" y "Actual_Delivery_Date" son puros nulos
    #"Submitted_for_Approval" puros valores nulos
    #"Prod_Category_A" tiene todos sus valores iguales
    df = df.drop(['Submitted_for_Approval','Last_Activity','Actual_Delivery_Date','Prod_Category_A'], axis=1)
    return df

def agregarColumnas(df):
    df['Closed'] = df['Stage'].replace({'Closed Won': True, 'Closed Lost': True, 'Negotiation':False,'Proposal':False,'Qualification':False})#REVISAR
    df['Won'] = df['Stage'].replace({'Closed Won': True, 'Closed Lost': False, 'Negotiation':False,'Proposal':False,'Qualification':False})
    convertirATipo(df,['Stage'],'category')
    return df

def correccionDeTerritorios(df):
    #se refiere a diferentes partes de usa
    df = df.replace({'Territory':{'Central US':'USA','NE America':'USA', 'NW America':'USA','SW America':'USA','SE America':'USA'}})
    #
    df = df.replace({'Territory':{'KSA':'Saudi Arabia'}})
    #No se ha encontrado la dorma de los siguientes datos 'Kosovo','South America', 'South East Asia', 'UAE (Dubai)', 'UAE (Others)' (en el caso de kosovo no lo grafica)
    return df

def preparacionDelDataFrame(df,entrenamiento=True):
    df = eliminarColumnasSinImportancia(df)
    df = establecerTipos(df)
    df = correccionDeTerritorios(df)
    df.rename(columns = {'Source ':'Source'}, inplace = True)
    #df = agregarHemisferios(df)#desactivado desde el readcsv
    if (entrenamiento):
      df = agregarColumnas(df)
    return df

### por oportunidad

In [86]:
def desacerseDeNulosDateTime(df,columna):
  df[columna] = df[columna].apply(lambda x: datetime.max if (x is None or x is np.NaN or x is pd.NaT) else x)
  return df

def descomposicionDeFechas(df,lista):
  """se nesesitan enteros no fechas"""
  for columna in lista:
    anio = columna + '_anio'
    df[anio] = df[columna].apply(lambda x: x if x is None else x.year)
    mes = columna + '_mes'
    df[mes] = df[columna].apply(lambda x: x if x is None else x.month)
    dia = columna + '_dia'
    df[dia] = df[columna].apply(lambda x: x if (x is None) else x.day)
  df = df.drop(lista, axis=1)
  return df

def establecerEstacion(df,columnaFecha):
  estacion = columnaFecha + '_Estacion'
  df[estacion] = 'Desconocido'
  df['temporalEstaciones'] = df[columnaFecha].apply(lambda x: 'Desconocido' if x is None else estaciones(x,True))
  df.loc[df['hemisferio'] == 'Norte' , estacion] = df['temporalEstaciones']
  df['temporalEstaciones'] = df[columnaFecha].apply(lambda x: 'Desconocido' if x is None else estaciones(x,False))
  df.loc[df['hemisferio'] == 'Sur' , estacion] = df['temporalEstaciones']
  df = df.drop(['temporalEstaciones'], axis=1)
  convertirATipo(df,[estacion],'category')
  return df

def estaciones(fecha,norte):
  if (norte):
    estaciones = ['primavera','verano','otoño','invierno']
  else:
    estaciones = ['otoño','invierno','primavera','verano']
  if (fecha.month == 12 and fecha.day >= 21 or fecha.month <= 3 and fecha.day < 21):
    return estaciones[3]
  elif (fecha.month == 9 and fecha.day >= 21 or fecha.month > 9):
    return estaciones[2]
  elif (fecha.month == 6 and fecha.day >= 21 or fecha.month > 6):
    return estaciones[1]
  elif (fecha.month == 3 and fecha.day >= 21 or fecha.month > 3):
    return estaciones[0]
  else:
    return 'Desconocido'

def diferenciaDeFechasEnDias(diferenciaDeFechas):
  return (diferenciaDeFechas.year * 365 + diferenciaDeFechas.month * 30 + diferenciaDeFechas.day)

def diferenciaEntreFechas(df,colFechaInicial,colFechaFinal):
  df['TiempoDeDiferencia'] = (df[colFechaFinal] - df[colFechaInicial])
  df['TiempoDeDiferencia'] = pd.to_numeric(df['TiempoDeDiferencia'].dt.days, downcast='integer')#revisar si se conviete totalmente a dias
  #df['TiempoDeDiferencia'] = df['TiempoDeDiferencia'].apply(lambda x: diferenciaDeFechasEnDias(x))
  df = df.drop([colFechaInicial,colFechaFinal], axis=1)
  return df

In [137]:
def dataEntrenamiento(df):
  data = df.groupby('Opportunity_ID').agg({'Won':'sum','Closed':'sum','modificaciones':'sum',
                                           #'Won':'sum','modificaciones':'sum',
                                           'Last_Modified_Date':'max','Opportunity_Created_Date':'min',
                                           #'Price':'mean',#Demaciados nulos
                                           #'Quote_Expiry_Date':'max',
                                           'Pricing, Delivery_Terms_Quote_Appr':'sum',
                                           'Pricing, Delivery_Terms_Approved':'sum',
                                           'Bureaucratic_Code_0_Approval':'sum',
                                           'Bureaucratic_Code_0_Approved':'sum',
                                           'Account_Created_Date':'min',
                                           'Total_Amount':'sum','Region':'first',
                                           'Territory':'first',
                                           'ASP_(converted)':'sum',
                                           'Account_Type':'first',
                                           'Delivery_Quarter':'first',
                                           'Product_Type':'first',
                                           'Product_Category_B':'first',
                                           'Billing_Country':'first',
                                           'Planned_Delivery_End_Date':'max',
                                           'Planned_Delivery_Start_Date':'min',
                                           'TRF':'mean'
                                           #'hemisferio':'first'
                                           })#hay que seguir agregando cosas que son importantes
  return data

def dataTesteo(df):
  data = df.groupby('Opportunity_ID').agg({'modificaciones':'sum',
                                           'Last_Modified_Date':'max','Opportunity_Created_Date':'min',
                                           #'Price':'mean',#Demaciados nulos
                                           #'Quote_Expiry_Date':'max',
                                           'Pricing, Delivery_Terms_Quote_Appr':'sum',
                                           'Pricing, Delivery_Terms_Approved':'sum',
                                           'Bureaucratic_Code_0_Approval':'sum',
                                           'Bureaucratic_Code_0_Approved':'sum',
                                           'Account_Created_Date':'min',
                                           'Total_Amount':'sum','Region':'first',
                                           'Territory':'first',
                                           'ASP_(converted)':'sum',
                                           'Account_Type':'first',
                                           'Delivery_Quarter':'first',
                                           'Product_Type':'first',
                                           'Product_Category_B':'first',
                                           'Billing_Country':'first',
                                           'Planned_Delivery_End_Date':'max',
                                           'Planned_Delivery_Start_Date':'min',
                                           'TRF':'mean'
                                           #'hemisferio':'first'
                                           })#hay que seguir agregando cosas que son importantes
  return data  

def agrupacionDeOportunidades(df,entrenamiento=True):
  df['modificaciones'] = 1
  if (entrenamiento):
    data = dataEntrenamiento(df)
    #Solo me interesa saber si se cerro con exito
    #data['Closed'] = data['Closed'].agg(lambda x: 1 if x > 0 else 0)
    data['Won'] = data['Won'].agg(lambda x: 1 if x > 0 else 0)
    #data['Lost'] = data['Closed'] - data['Won']#si es won es closed pero si es closed y no es won es perdido
    #data['Lost'] = data['Lost'].agg(lambda x: 1 if x > 0 else 0)

    #REVISAR la importancia del caso no cerrado
    data = data[data['Closed'] > 0]#no interesan los que no se cerraron, dado que no se cerraron no aportan
    data = data.drop(['Closed'], axis=1)
  else:
    data = dataTesteo(df)

  data['Pricing, Delivery_Terms_Quote_Appr'] = data['Pricing, Delivery_Terms_Quote_Appr'].agg(lambda x: 1 if x > 0 else 0)
  data['Pricing, Delivery_Terms_Approved'] = data['Pricing, Delivery_Terms_Approved'].agg(lambda x: 1 if x > 0 else 0)
  data['Bureaucratic_Code_0_Approval'] = data['Bureaucratic_Code_0_Approval'].agg(lambda x: 1 if x > 0 else 0)
  data['Bureaucratic_Code_0_Approved'] = data['Bureaucratic_Code_0_Approved'].agg(lambda x: 1 if x > 0 else 0)
  #data = data.replace({'Won':})

  #categoricas
  #listaDeColumnasCategoricas = ['Account_Type','Region','Territory','Delivery_Quarter']
  listaDeColumnasCategoricas = ['Account_Type','Region','Territory','Billing_Country',
                                'Delivery_Quarter','Product_Type','Product_Category_B']
  convertirATipo(data,listaDeColumnasCategoricas,'category')

  #data = establecerEstacion(data,'Opportunity_Created_Date')
  #data = establecerEstacion(data,'Quote_Expiry_Date')
  #data = desacerseDeNulosDateTime(data,'Quote_Expiry_Date')#si no hay fecha de expiracion se pre supone que es infinita

  listaDeValoresDeFechas = ['Last_Modified_Date','Opportunity_Created_Date',
                            'Account_Created_Date']
  data = descomposicionDeFechas(data,listaDeValoresDeFechas)

  #enteros
  #listaDeColumnasEnteras = ['Quote_Expiry_Date_anio','Quote_Expiry_Date_mes','Quote_Expiry_Date_dia']
  #convertirATipo(data,listaDeColumnasEnteras,'int')
  #data = agregarHemisferios(data)

  #data = data.drop(['hemisferio'], axis=1)

  data = diferenciaEntreFechas(data,'Planned_Delivery_Start_Date','Planned_Delivery_End_Date')

  return data

las siguientes columnas no fueron probadas hay que analizarlas

Posibles columnas a usar:

- Bureaucratic_Code
- Delivery_Terms
- Delivery_Year (posibles datos repetidos)
- Month (posibles datos repetidos)
- Opportunity_Owner
- Opportunity_Type
- Product_Family
- Product_Name
- Quote_Type (muy desbalanceado)

Revisar el contexto

- Total_Amount_Currency
- Total_Taxable_Amount
- Total_Taxable_Amount_Currency
- ASP
- ASP_(converted)_Currency
- ASP_Currency


las columnas con gran catidad de nones parecen afectar positivamente el resultado hay que revisarlas una por una

- Currency: Excesiva cantidad de nones
- Brand: Excesiva cantidad de nones
- Sales_Contract_No: Excesiva cantidad de nones
- Size: Excesiva cantidad de nones
- Source: Excesiva cantidad de nones

In [68]:
#agrupacionEntrenamiento['hemisferio'].count() - agrupacionEntrenamiento['Billing_Country'].count()
#agrupacionTesteo['Billing_Country'].value_counts().to_csv('asd.csv')

listaDeCategoricas = ['Region','Territory','Product_Type','Product_Category_B',
                      'Account_Type','Delivery_Quarter','Billing_Country']
for col in agrupacionEntrenamiento.columns:
  if (col in listaDeCategoricas): continue
  print(col)
  agrupacionEntrenamiento[col].astype('float')

Won
modificaciones
Pricing, Delivery_Terms_Quote_Appr
Pricing, Delivery_Terms_Approved
Bureaucratic_Code_0_Approval
Bureaucratic_Code_0_Approved
Total_Amount
ASP_(converted)
Last_Modified_Date_anio
Last_Modified_Date_mes
Last_Modified_Date_dia
Opportunity_Created_Date_anio
Opportunity_Created_Date_mes
Opportunity_Created_Date_dia
Account_Created_Date_anio
Account_Created_Date_mes
Account_Created_Date_dia
Quote_Expiry_Date_anio
Quote_Expiry_Date_mes
Quote_Expiry_Date_dia
TiempoDeDiferencia


## Ejecucion de cambios

### ejecucion por modificaciones de oportunidad

In [120]:
entrenamientoProcesado = preparacionDelDataFrame(entrenamiento)
entrenamientoProcesado.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16947 entries, 0 to 16946
Data columns (total 50 columns):
 #   Column                              Non-Null Count  Dtype         
---  ------                              --------------  -----         
 0   ID                                  16947 non-null  int64         
 1   Region                              16947 non-null  category      
 2   Territory                           16947 non-null  object        
 3   Pricing, Delivery_Terms_Quote_Appr  16947 non-null  bool          
 4   Pricing, Delivery_Terms_Approved    16947 non-null  bool          
 5   Bureaucratic_Code_0_Approval        16947 non-null  bool          
 6   Bureaucratic_Code_0_Approved        16947 non-null  bool          
 7   Bureaucratic_Code                   16947 non-null  category      
 8   Account_Created_Date                16947 non-null  datetime64[ns]
 9   Source                              16947 non-null  category      
 10  Billing_Country       

In [121]:
testeoProsesado = preparacionDelDataFrame(testeo,False)
testeoProsesado.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2551 entries, 0 to 2550
Data columns (total 47 columns):
 #   Column                              Non-Null Count  Dtype         
---  ------                              --------------  -----         
 0   ID                                  2551 non-null   int64         
 1   Region                              2551 non-null   category      
 2   Territory                           2551 non-null   object        
 3   Pricing, Delivery_Terms_Quote_Appr  2551 non-null   bool          
 4   Pricing, Delivery_Terms_Approved    2551 non-null   bool          
 5   Bureaucratic_Code_0_Approval        2551 non-null   bool          
 6   Bureaucratic_Code_0_Approved        2551 non-null   bool          
 7   Bureaucratic_Code                   2551 non-null   category      
 8   Account_Created_Date                2551 non-null   datetime64[ns]
 9   Source                              2551 non-null   category      
 10  Billing_Country         

### ejecucion por oportunidad

In [122]:
agrupacionEntrenamiento = agrupacionDeOportunidades(entrenamientoProcesado)
agrupacionEntrenamiento.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9791 entries, 0 to 12803
Data columns (total 26 columns):
 #   Column                              Non-Null Count  Dtype   
---  ------                              --------------  -----   
 0   Won                                 9791 non-null   int64   
 1   modificaciones                      9791 non-null   int64   
 2   Pricing, Delivery_Terms_Quote_Appr  9791 non-null   int64   
 3   Pricing, Delivery_Terms_Approved    9791 non-null   int64   
 4   Bureaucratic_Code_0_Approval        9791 non-null   int64   
 5   Bureaucratic_Code_0_Approved        9791 non-null   int64   
 6   Total_Amount                        9791 non-null   float64 
 7   Region                              9791 non-null   category
 8   Territory                           9791 non-null   category
 9   ASP_(converted)                     9791 non-null   float64 
 10  Account_Type                        9791 non-null   category
 11  Delivery_Quarter             

In [123]:
agrupacionTesteo = agrupacionDeOportunidades(testeoProsesado,False)
agrupacionTesteo.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1567 entries, 10689 to 12368
Data columns (total 25 columns):
 #   Column                              Non-Null Count  Dtype   
---  ------                              --------------  -----   
 0   modificaciones                      1567 non-null   int64   
 1   Pricing, Delivery_Terms_Quote_Appr  1567 non-null   int64   
 2   Pricing, Delivery_Terms_Approved    1567 non-null   int64   
 3   Bureaucratic_Code_0_Approval        1567 non-null   int64   
 4   Bureaucratic_Code_0_Approved        1567 non-null   int64   
 5   Total_Amount                        1567 non-null   float64 
 6   Region                              1567 non-null   category
 7   Territory                           1567 non-null   category
 8   ASP_(converted)                     1567 non-null   float64 
 9   Account_Type                        1567 non-null   category
 10  Delivery_Quarter                    1567 non-null   category
 11  Product_Type             

### separacion de resultados de entrenamiento

In [124]:
entrenamientoResultado = agrupacionEntrenamiento[['Won']]
entrenamientoResultado.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9791 entries, 0 to 12803
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype
---  ------  --------------  -----
 0   Won     9791 non-null   int64
dtypes: int64(1)
memory usage: 153.0 KB


In [125]:
agrupacionEntrenamiento = agrupacionEntrenamiento.drop(['Won'], axis=1)
agrupacionEntrenamiento.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9791 entries, 0 to 12803
Data columns (total 25 columns):
 #   Column                              Non-Null Count  Dtype   
---  ------                              --------------  -----   
 0   modificaciones                      9791 non-null   int64   
 1   Pricing, Delivery_Terms_Quote_Appr  9791 non-null   int64   
 2   Pricing, Delivery_Terms_Approved    9791 non-null   int64   
 3   Bureaucratic_Code_0_Approval        9791 non-null   int64   
 4   Bureaucratic_Code_0_Approved        9791 non-null   int64   
 5   Total_Amount                        9791 non-null   float64 
 6   Region                              9791 non-null   category
 7   Territory                           9791 non-null   category
 8   ASP_(converted)                     9791 non-null   float64 
 9   Account_Type                        9791 non-null   category
 10  Delivery_Quarter                    9791 non-null   category
 11  Product_Type                 

## Prueva

In [ ]:
prueva = agrupacionTesteo.reset_index()
prueva = prueva[['Opportunity_ID']]
prueva['prediccion'] = 0.5
prueva
prueva.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1567 entries, 0 to 1566
Data columns (total 2 columns):
 #   Column          Non-Null Count  Dtype
---  ------          --------------  -----
 0   Opportunity_ID  1567 non-null   int64
 1   prediccion      1567 non-null   int64
dtypes: int64(2)
memory usage: 24.6 KB


In [ ]:
prueva = agrupacionTesteo
prueva['Target'] = 0.5
prueva = prueva[['Target']]
prueva.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1567 entries, 10689 to 12368
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Target  1567 non-null   float64
dtypes: float64(1)
memory usage: 24.5 KB


In [ ]:
from google.colab import files

prueva.to_csv('prueva.csv')
#files.download('resultado.csv')

## Resultado

In [20]:
def generarResultado(df,prediccion):
  resultado = df
  resultado['Target'] = prediccion
  resultado = resultado[['Target']]
  resultado.to_csv('resultado.csv')
  return resultado

In [21]:
def auxiliarUnificarValor(arreglo):
  return arreglo[:,0]

## Catboost

### grid search

In [145]:
def GridSearchCatboost(train_data_o,train_labels,cat_features):
  """clf = CatBoostClassifier()
  params = {'iterations': [500],
            'depth': [4, 5, 6],
            #'loss_function': ['Logloss', 'CrossEntropy'],
            'l2_leaf_reg': np.logspace(-10, 1, 50),
            'leaf_estimation_iterations': [10],
            'learning_rate': [0.5,0.25,0.05],
            'rsm' : [0.7,0.5]
            #'eval_metric': ['Accuracy'],
            #'use_best_model': ['True'],
            #'logging_level':['Silent'],
            #'random_seed': [42]
          }
  scorer = make_scorer(accuracy_score)
  clf_grid = GridSearchCV(estimator=clf, param_grid=params, scoring=scorer, cv=5)
  clf_grid.fit(X_train_enc, y_train,cat_features)
  best_param = clf_grid.best_params_
  return best_param"""
  model = CatBoostClassifier(loss_function='Logloss')
  #model = CatBoostClassifier(loss_function='CrossEntropy')

  train_data = train_data_o
  # convert categorical columns to integers
  for header in cat_features:
    train_data[header] = train_data[header].astype('category').cat.codes

  grid = {'learning_rate': list(np.arange(0.05,0.51,0.05)),
          'depth': list(range(6,13,2)),
          'l2_leaf_reg': list(np.arange(2,5.1,0.5)),
          'iterations': list(range(10,101,15)),
          'rsm':list(np.arange(0.1,1.1,0.1))
          }

  grid_search_result = model.grid_search(grid, 
                                        X=train_data, 
                                        y=train_labels,
                                        cv=10,
                                        plot=True)
  
  return grid_search_result

In [146]:
listaDeCategoricas = ['Region','Territory','Product_Type','Product_Category_B',
                      'Account_Type','Delivery_Quarter','Billing_Country']
#listaDeCategoricas = []
valores = GridSearchCatboost(agrupacionEntrenamiento,entrenamientoResultado,listaDeCategoricas)
valores

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Se truncaron las últimas líneas 5000 del resultado de transmisión.

bestTest = 0.3602252463
bestIteration = 78

8765:	loss: 0.3602252	best: 0.3394048 (7342)	total: 2h 16m 57s	remaining: 2h 49m 16s

bestTest = 0.3688916005
bestIteration = 76

8766:	loss: 0.3688916	best: 0.3394048 (7342)	total: 2h 16m 59s	remaining: 2h 49m 16s

bestTest = 0.3762368185
bestIteration = 69

8767:	loss: 0.3762368	best: 0.3394048 (7342)	total: 2h 17m	remaining: 2h 49m 15s

bestTest = 0.3795733814
bestIteration = 24

8768:	loss: 0.3795734	best: 0.3394048 (7342)	total: 2h 17m 2s	remaining: 2h 49m 16s

bestTest = 0.3924922678
bestIteration = 27

8769:	loss: 0.3924923	best: 0.3394048 (7342)	total: 2h 17m 3s	remaining: 2h 49m 15s

bestTest = 0.3801928237
bestIteration = 99

8770:	loss: 0.3801928	best: 0.3394048 (7342)	total: 2h 17m 5s	remaining: 2h 49m 15s

bestTest = 0.3651290685
bestIteration = 98

8771:	loss: 0.3651291	best: 0.3394048 (7342)	total: 2h 17m 7s	remaining: 2h 49m 16s

bestTest = 0.3511792297
bestIt

KeyboardInterrupt: ignored

### prediccion

In [22]:
def catboost(train_data,train_labels,cat_features,eval_data):
  # Inicializador de CatBoostClassifier
  model = CatBoostClassifier(iterations=10,
                             learning_rate=0.5,
                             depth=8,
                             l2_leaf_reg=3.5,
                             rsm=0.7
                             #use_best_model=True#Requiere data de evalucion
                             )
  #parametros importantes por agregar: l2_leaf_reg, rsm
  #para tipos de category: cat_features, one_hot_max_size

  # Entrenamiento del modelo
  model.fit(train_data, train_labels, cat_features)

  # obtener prediccion
  #preds_class = model.predict(eval_data)

  # obtener probabilidad de prediccion
  preds_proba = model.predict_proba(eval_data)

  # obtener RawFormulaVal de la prediccion
  #preds_raw = model.predict(eval_data, prediction_type='RawFormulaVal')

  #return resultado(eval_data,preds_proba)
  return preds_proba

In [134]:
#listaDeCategoricas = ['Region','Territory','Product_Type','Product_Category_B']
#listaDeCategoricas = ['Region','Territory','Product_Type','Product_Category_B','Account_Type','Delivery_Quarter']
listaDeCategoricas = ['Region','Territory','Product_Type','Product_Category_B',
                      'Account_Type','Delivery_Quarter','Billing_Country']
#listaDeCategoricas = []
res = catboost(agrupacionEntrenamiento,entrenamientoResultado,listaDeCategoricas,agrupacionTesteo)
res

0:	learn: 0.5076148	total: 15.8ms	remaining: 142ms
1:	learn: 0.4584729	total: 30.9ms	remaining: 124ms
2:	learn: 0.4238337	total: 47.3ms	remaining: 110ms
3:	learn: 0.4033573	total: 63.3ms	remaining: 94.9ms
4:	learn: 0.3916173	total: 78.7ms	remaining: 78.7ms
5:	learn: 0.3837409	total: 93.6ms	remaining: 62.4ms
6:	learn: 0.3775121	total: 109ms	remaining: 46.5ms
7:	learn: 0.3651020	total: 123ms	remaining: 30.7ms
8:	learn: 0.3589807	total: 138ms	remaining: 15.3ms
9:	learn: 0.3517698	total: 152ms	remaining: 0us


array([[0.42017963, 0.57982037],
       [0.72392187, 0.27607813],
       [0.27017609, 0.72982391],
       ...,
       [0.74721679, 0.25278321],
       [0.43799496, 0.56200504],
       [0.92075364, 0.07924636]])

In [135]:
resultado = auxiliarUnificarValor(res)
resultado = (resultado - 1) * (-1)#En las ultimas pruevas es el opuesto el que genera mejor resultado
resultado

array([0.57982037, 0.27607813, 0.72982391, ..., 0.25278321, 0.56200504,
       0.07924636])

In [136]:
dataResultante = generarResultado(agrupacionTesteo,resultado)
dataResultante.head()

Target
Opportunity_ID                     
10689                          0.58
10690                          0.28
10691                          0.73
10692                          0.76
10693                          0.79

## LightGBM

In [ ]:
def lightGBM(train_data,train_labels,cat_features,eval_data):
  # evaluate the model
  model = lgb.LGBMClassifier()
  cv = RepeatedStratifiedKFold(n_splits=10, n_repeats=3, random_state=1)
  n_scores = cross_val_score(model,
                             train_data,
                             train_labels,
                             scoring='accuracy',
                             cv=cv,
                             n_jobs=-1,
                             categorical_feature=cat_features,
                             error_score='raise')
  print('Accuracy: %.3f (%.3f)' % (mean(n_scores), std(n_scores)))
  # fit the model on the whole dataset
  model = lgb.LGBMClassifier()
  model.fit(X, y)
  # make a single prediction
  yhat = model.predict(eval_data)
  return yhat
"""
  parameters = {
      'application': 'binary',
      'objective': 'binary',
      'metric': 'auc',
      'is_unbalance': 'true',
      'boosting': 'gbdt',
      'num_leaves': 31,
      'feature_fraction': 0.5,
      'bagging_fraction': 0.5,
      'bagging_freq': 20,
      'learning_rate': 0.05,
      'verbose': 0,
      'categorical_feature':cat_features
  }

  model = lgb.train(parameters,
                        train_data,
                        valid_sets=train_labels,
                        num_boost_round=5000,
                        early_stopping_rounds=100)

  x = eval_data
  y = model.predict(x)
  output = pd.DataFrame({'id': ids, 'target': y})
"""
  #output.to_csv("submission.csv", index=False)
  # save model to file
  #gbm.save_model('model.txt')

"\n  parameters = {\n      'application': 'binary',\n      'objective': 'binary',\n      'metric': 'auc',\n      'is_unbalance': 'true',\n      'boosting': 'gbdt',\n      'num_leaves': 31,\n      'feature_fraction': 0.5,\n      'bagging_fraction': 0.5,\n      'bagging_freq': 20,\n      'learning_rate': 0.05,\n      'verbose': 0,\n      'categorical_feature':cat_features\n  }\n\n  model = lgb.train(parameters,\n                        train_data,\n                        valid_sets=train_labels,\n                        num_boost_round=5000,\n                        early_stopping_rounds=100)\n\n  x = eval_data\n  y = model.predict(x)\n  output = pd.DataFrame({'id': ids, 'target': y})\n"

In [ ]:
listaDeCategoricas = ['Region','Territory','Product_Type','Product_Category_B','Account_Type','Delivery_Quarter','Billing_Country']
res = lightGBM(agrupacionEntrenamiento,entrenamientoResultado,listaDeCategoricas,agrupacionTesteo)
res

TypeError: ignored